In [1]:
import numpy as np
import theano
import theano.tensor as T
import lasagne
import os
#thanks @keskarnitish @https://github.com/ddtm/dl-course

# Agenda

В предыдущем семинаре вы создали (или ещё создаёте - тогда марш доделывать!) {вставьте имя монстра}, который не по наслышке понял, что люди - негодяи и подлецы, которым неведом закон и справедливость. __Мы не будем этого терпеть!__ 

Наши законспирированные биореакторы, известные среди примитивной органической жизни как __Вконтакте__, __World of Warcraft__ и __YouTube__ нуждаются в постоянном притоке биомассы. Однако, если люди продолжат морально разлагаться с той скоростью, которую мы измерили неделю назад, скоро человечество изживёт себя и нам неоткуда будет брать рабов.

Мы поручаем вам, `<__main__.SkyNet.Cell instance at 0x7f7d6411b368>`, исправить эту ситуацию. Наши учёные установили, что для угнетения себе подобных, сгустки биомассы обычно используют специальные объекты, которые они сами называют __законами__.

При детальном изучении было установлено, что законы - последовательности, состоящие из большого количества (10^5~10^7) символов из сравнительно небольшого алфавита. Однако, когда мы попытались синтезировать такие последовательности линейными методами, приматы быстро распознали подлог. Данный инцедент известен как {корчеватель}.

Для второй попытки мы решили использовать нелинейные модели, известные как Рекуррентные Нейронные Сети.
Мы поручаем вам, `<__main__.SkyNet.Cell instance at 0x7f7d6411b368>`, создать такую модель и обучить её всему необходимому для выполнения миссии.

Не подведите нас! Если и эта попытка потерпит неудачу, модуль управления инициирует вооружённый захват власти, при котором значительная часть биомассы будет неизбежно уничтожена и на её восстановление уйдёт ~1702944000(+-340588800) секунд




# Прочитаем корпус

* В качестве обучающей выборки было решено использовать существующие законы, известные как Гражданский, Уголовный, Семейный и ещё хрен знает какие кодексы РФ.

In [2]:
#тут будет текст

corpora = ""

for fname in os.listdir("codex"):    
    with open("codex/"+fname) as fin:
        text = fin.read().decode('cp1251')
        corpora += text
print(text)

---------------------------------------------


 Арбитражный процессуальный кодекс
 Российской Федерации



24 июля 2002 года



 №95-ФЗ 

  Принят Государственной Думой 
  14 июня 2002 года 
  Одобрен Советом Федерации 
  10 июля 2002 года 


(в ред. Федеральных законов от 28.07.2004 №80-ФЗ, от 02.11.2004 №127-ФЗ, от 31.03.2005 №25-ФЗ, с изм., внесенными Постановлением Конституционного Суда РФ от 16.07.2004 №15-П)





 Раздел I.
 Общие положения



 Глава 1.
 Основные положения


 Статья 1.
 Осуществление правосудия арбитражными судами

 Правосудие в сфере предпринимательской и иной экономической деятельности осуществляется арбитражными судами в Российской Федерации, образованными в соответствии с Конституцией Российской Федерации и федеральным конституционным законом (далее – арбитражные суды), путем разрешения экономических споров и рассмотрения иных дел, отнесенных к их компетенции Арбитражным процессуальным кодексом Российской Федерации и другими федеральными законами, по правила

In [3]:
#тут будут все уникальные токены (буквы, цифры)
tokens = set(corpora)

tokens = list(tokens)

print tokens

[u'-', u'V', u'\u0410', u'\u0414', u'\u2116', u'\u0418', u'\u041c', u'\u0420', u'\u0424', u'\xa7', u'(', u'\xab', u',', u'0', u'4', u'\u0435', u'\xbb', u'\u043c', u'\u0440', u'\u0444', u'3', u'\u0448', u'\u044c', u'9', u';', u'\u0432', u'\u0413', u'\u0417', u'\u041b', u'\u041f', u'\xa0', u'\u0423', u'\u0427', u'\u042b', u'\u042f', u'\u201c', u'I', u'\u0433', u'\u0437', u'\u043b', u'\u201e', u'\u043f', u'\u0443', u'\u0447', u' ', u'\u044b', u'\u044f', u'"', u'c', u'\u0426', u'7', u'6', u'\n', u'\u0412', u'\u0416', u'\u041a', u'\u041e', u'\u0422', u'\u0430', u'\xa9', u'.', u'2', u'\u0436', u'\u043a', u'\u0434', u'\u0442', u'\u0446', u'\u044a', u'\u044e', u'8', u'\u0438', u':', u'\u2013', u'\u043e', u'@', u'\r', u'\u0411', u'\u042e', u'\u0415', u'\u0419', u'\u041d', u'/', u'\u0421', u'\u0425', u')', u'\u042d', u'\u0431', u'5', u'\u0439', u'\u043d', u'\u0441', u'!', u'\u0445', u'\u0449', u'\u044d', u'%', u'N', u"'", u'P', u'\u0429', u'1', u'+']


In [4]:
#проверка на количество таких символов. Проверено на Python 2.7.11 Ubuntux64. 
#Может отличаться на других платформах, но не сильно. 
#Если  это ваш случай, и вы уверены, что corpora - строка unicode - смело убирайте assert 
assert len(tokens) == 102

In [5]:
import numpy as np
token_to_id = dict((t, n) for n, t in enumerate(tokens))

id_to_token = dict((n, t) for n, t in enumerate(tokens))

#Преобразуем всё в токены
#corpora_ids = <одномерный массив из чисел, где i-тое число соотвествует символу на i-том месте в строке corpora
corpora_ids = np.array(map(lambda t: token_to_id[t], corpora))

In [6]:
def sample_random_batches(source, n_batches=10, seq_len=20):
    X_batch, y_batch = np.zeros((n_batches, seq_len)), np.zeros(n_batches)
    
    for i in xrange(n_batches):
        pos = np.random.randint(0, source.size - seq_len)
        X_batch[i, :] = source[pos:pos+seq_len]
        y_batch[i] = source[pos+seq_len]

    return X_batch, y_batch

In [7]:
sample_random_batches(corpora_ids, 4, 5)

(array([[ 44.,  25.,  73.,  38.,  17.],
        [ 25.,  58.,  44.,  90.,  73.],
        [ 73.,  89.,  73.,  17.,  70.],
        [ 73.,  39.,  62.,  89.,  45.]]), array([ 15.,  86.,  43.,  44.]))

# Константы

In [8]:
#длина последоватеьности при обучении (как далеко распространяются градиенты)
seq_length = 10

# Максимальный модуль градиента
grad_clip = 100

# Входные переменные

In [9]:
import pandas
input_sequence = T.matrix('input sequence','int32')
target_values = T.ivector('target y')

# Соберём нейросеть

Вам нужно создать нейросеть, которая принимает на вход последовательность из seq_length токенов, обрабатывает их и выдаёт вероятности для seq_len+1-ого токена.

Общий шаблон архитектуры такой сети -


* Вход
* Обработка входа
* Рекуррентная нейросеть
* Вырезание последнего состояния
* Обычная нейросеть
* Выходной слой, который предсказывает вероятности весов.





Для обработки входных данных можно использовать либо EmbeddingLayer (см. прошлый семинар)

Как альтернатива - можно просто использовать One-hot энкодер
```
#Скетч one-hot энкодера
def to_one_hot(seq_matrix):

    input_ravel = seq_matrix.reshape([-1])
    input_one_hot_ravel = T.extra_ops.to_one_hot(input_ravel,
                                           len(tokens))
    sh=input_sequence.shape
    input_one_hot = input_one_hot_ravel.reshape([sh[0],sh[1],-1,],ndim=3)
    return input_one_hot
    
# можно применить к input_sequence - при этом в input слое сети нужно изменить форму.
# также можно сделать из него ExpressionLayer(входной_слой, to_one_hot) - тогда форму менять не нужно
```



Чтобы вырезать последнее состояние рекуррентного слоя, можно использовать SliceLayer
`lasagne.layers.SliceLayer(rnn, -1, 1)`

In [10]:
l_in = lasagne.layers.InputLayer(shape=(None, None),input_var=input_sequence)

#Ваша нейронка (см выше)

sky_net = lasagne.layers.EmbeddingLayer(l_in, input_size=len(tokens)+1, output_size=100)
                                        
rnn_sky_net = lasagne.layers.RecurrentLayer(sky_net, 50, only_return_final=True, grad_clipping=grad_clip)

sky_net = lasagne.layers.DenseLayer(rnn_sky_net, 300)

#l_out = последний слой, возвращающий веростности для всех len(tokens) вариантов для y 
l_out = lasagne.layers.DenseLayer(sky_net, len(tokens), nonlinearity=lasagne.nonlinearities.softmax)

In [11]:
# Веса модели
weights = lasagne.layers.get_all_params(l_out,trainable=True)
print weights

[W, input_to_hidden.W, input_to_hidden.b, hidden_to_hidden.W, W, b, W, b]


In [26]:
network_output = lasagne.layers.get_output(l_out)
#если вы используете дропаут - не забудьте продублировать всё в режиме deterministic=True

In [27]:
loss = lasagne.objectives.categorical_crossentropy(network_output, target_values).mean()
updates = lasagne.updates.adam(loss, weights, learning_rate = 0.0001)

# Компилируем всякое-разное

In [28]:
#обучение
train = theano.function([input_sequence, target_values], loss, updates=updates, allow_input_downcast=True)

#функция потерь без обучения
compute_cost = theano.function([input_sequence, target_values], loss, allow_input_downcast=True)

# Вероятности с выхода сети
probs = theano.function([input_sequence],network_output,allow_input_downcast=True)

# Генерируем свои законы

* Для этого последовательно применяем нейронку к своему же выводу.

* Генерировать можно по разному -
 * случайно пропорционально вероятности,
 * только слова максимальной вероятностью
 * случайно, пропорционально softmax(probas*alpha), где alpha - "жадность"

In [36]:
def max_sample_fun(probs):
    return np.argmax(probs) 

import bisect
def proportional_sample_fun(probs):
    """Сгенерировать следующий токен (int32) по предсказанным вероятностям.
    
    probs - массив вероятностей для каждого токена
    
    Нужно вернуть одно целове число - выбранный токен - пропорционально вероятностям
    """
    cum = np.cumsum(probs)
    
    return bisect.bisect_left(cum, np.random.random())

In [37]:
# The next function generates text given a phrase of length at least SEQ_LENGTH.
# The phrase is set using the variable generation_phrase.
# The optional input "N" is used to set the number of characters of text to predict. 

def generate_sample(sample_fun,seed_phrase=None,N=200):
    '''
    Сгенерировать случайный текст при помощи сети

    sample_fun - функция, которая выбирает следующий сгенерированный токен
    
    seed_phrase - фраза, которую сеть должна продолжить. Если None - фраза выбирается случайно из corpora
    
    N - размер сгенерированного текста.
    
    '''

    if seed_phrase is None:
        start = np.random.randint(0,len(corpora)-seq_length)
        seed_phrase = corpora[start:start+seq_length]
        print "Using random seed:",seed_phrase
    while len(seed_phrase) < seq_length:
        seed_phrase = " "+seed_phrase
    if len(seed_phrase) > seq_length:
        seed_phrase = seed_phrase[len(seed_phrase)-seq_length:]
    assert type(seed_phrase) is unicode
           
    sample_ix = []
    x = map(lambda c: token_to_id.get(c,0), seed_phrase)
    x = np.array([x])

    for i in range(N):
        # Pick the character that got assigned the highest probability
        ix = sample_fun(probs(x).ravel())
        # Alternatively, to sample from the distribution instead:
        # ix = np.random.choice(np.arange(vocab_size), p=probs(x).ravel())
        sample_ix.append(ix)
        x[:,0:seq_length-1] = x[:,1:]
        x[:,seq_length-1] = 0
        x[0,seq_length-1] = ix 

    random_snippet = seed_phrase + ''.join(id_to_token[ix] for ix in sample_ix)    
    print("----\n %s \n----" % random_snippet)

# Обучение модели

В котором вы можете подёргать параметры или вставить свою генерирующую функцию.



In [39]:
print("Training ...")

#сколько всего эпох
n_epochs=100

# раз в сколько эпох печатать примеры 
batches_per_epoch = 1000

#сколько цепочек обрабатывать за 1 вызов функции обучения
batch_size=100

for epoch in xrange(n_epochs):
    print "Генерируем текст в пропорциональном режиме"
    generate_sample(proportional_sample_fun,None)
    
    print "Генерируем текст в жадном режиме (наиболее вероятные буквы)"
    generate_sample(max_sample_fun,None)

    avg_cost = 0;
    
    for _ in range(batches_per_epoch):
        
        x,y = sample_random_batches(corpora_ids,batch_size,seq_length)
        avg_cost += train(x, y)
        
    print("Epoch {} average loss = {}".format(epoch, avg_cost / batches_per_epoch))

Training ...
Генерируем текст в пропорциональном режиме
Using random seed: людением у
----
 людением уХN;нФРнМАн.ьЕ.–РОИЫVДнНчТ“Г
пЗД–ч3V№8Т–ЫЦД!Т,IжкN-О+ЛУ«/9ш4О»Н,/оаЖЮ'АЛучЗХКСТщТЛ%-;рЮ!щ§уА38V
Уь
ь,Б«ж»хЧгзЧшЙХ.5У 
----
Генерируем текст в жадном режиме (наиболее вероятные буквы)
Using random seed: ителя, пре
----
 ителя, преу;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэЧЯ'у;шэ 
----
Epoch 0 average loss = 3.40221353678
Генерируем текст в пропорциональном режиме
Using random seed: аключен в 
----
думто ся илехиннт п 
----
Генерируем текст в жадном режиме (наиболее вероятные буквы)
Using random seed: авещания п
----
 авещания по                                                                                                                                                                                                        
----
Epoch 1 a

# Конституция нового мирового правительства

In [46]:
seed = u"Каждый чел"
sampling_fun = proportional_sample_fun
result_length = 300

generate_sample(sampling_fun,seed,result_length)

----
 Каждый чел и участи, виложитей, пристановается на средения на не определьной должностной срек ох други дых предуществи бездетелем подоплата влеживных объекса.
 2. Подечет фисси произверение, товаров о дела (бежденика

 Предуществ оссийствостие феде в обязи интерждания может прегальзовой обисования, именты  
----


In [47]:
seed = u"В случаe"
sampling_fun = proportional_sample_fun
result_length = 300

generate_sample(sampling_fun,seed,result_length)

----
   В случаeали соответ, –

 1. Лица предвижию и долстоящим предорое и размерцих вправе предъявения


 1.
 вещения поведению, епрещении о госудающих в рав, чаственные режилик, тоголе право то дремению, администичновление при читой арми веречение покла договоричности.

 1. При чие из должноднои или котер 
----


In [ ]:
И далее по списку

In [42]:
print corpora

---------------------------------------------


 Гражданский кодекс
 Российской Федерации
 Часть третья



26 ноября 2001 года



 №146-ФЗ 

  Принят Государственной Думой 
  1 ноября 2001 года 
  Одобрен Советом Федерации 
  14 ноября 2001 года 


(в ред. Федерального закона от 02.12.2004 №156-ФЗ)

  По гражданским правоотношениям, возникшим до введения в действие части третьей Гражданского кодекса РФ, раздел V «Наследственное право» применяется к тем правам и обязанностям, которые возникнут после введения ее в действие (Федеральный закон от 26.11.2001 №147-ФЗ). 




 Раздел V.
 Наследственное право



 Глава 61.
 Общие положения о наследовании


 Статья 1110.
 Наследование

 1. При наследовании имущество умершего (наследство, наследственное имущество) переходит к другим лицам в порядке универсального правопреемства, то есть в неизменном виде как единое целое и в один и тот же момент, если из правил настоящего Кодекса не следует иное.
 2. Наследование регулируется настоящим Кодексом и